## ELEX 4653 Lab 1

This lab provides practice on expressions, lists, dictionaries, control flow statements and functions.

Instructions:

- Modify this notebook by adding the Python code described below.

- Test your code using the menu item `Run ► Run All Cells`

- Save the notebook (the .ipynb file) and upload it to the appropriate Assignment folder on the course web site.

Version 3: corrected argument names in Question 3 description.  Corrected checking code for Question 2.

#### Question 1

Write a function, `area(r)` that returns the area of a circle of radius `r`.  For example `area(1.414)`should return `6.281`.... 

#### Question 2


Write a function, `noshout(l)`, where `l` is a list of `str`ings.  The function should delete from `l` any strings that are in ALL CAPS.  

For example, if the list `l` contains `['Hello', 'world!', 'YES NO', "Maybe"]` `noshout(l)` should modify `l` so that it contains `['Hello', 'world!', "Maybe"]`.  `noshout()` should not return a value.  *Hints: str.isupper(), don't use del()*.

#### Question 3

Write a function, `dfilt(d,f)`, where `d` is a dict and `f` is a list.  The function should return a `dict` consisting of the *key*`:`*value* pairs in `d` whose key appears in `f`.

For example, `dfilt({1:'a',2:'b',7:'lucky','x':'0'},['x',1,7,5])`should return `{1:'a',7:'lucky','x':0}` (with the items in any order).

#### Question 4

Write a function `hms(t)` that takes a numeric argument `t` and returns a 3-element tuple `(h,m,s)`.  `h`, `m`, and `s` are the hours, minutes and seconds elapsed during `t` seconds. For example, if `t` is 7000.5 then `hms(t)` should return `(1, 56, 40.5)`.

#### Question 5

Write a function `areasum(l)` that computes and returns the sum of the areas of rectangles whose width and height are given by the 2-element tuples in `l`.  For example, `areasum([(1,1), (2,3), (3,1.5)])` would return `11.5`.    

In [ ]:
# lab validation code; do not modify
def labcheck(testing=0,ntest=10):
    '''
    Python exercise checking.
    Ed.Casas 2023-5-22
    Calls functions q<n>* and checks HMAC of return value[0].
    On mismatch prints return value[1] (function, arguments and return values).
    Setting testing=1 prints HMACs of correct results; paste into 'hashvalues'.
    Note:
    If q<n>* result not JSON-able, convert to string.
    Result order matters for comparison. Sort result if ordering not important.
    '''
    
    import base64, copy, hashlib, json, random, re, string, types 
    from random import randint
    
    # compare regex to strings that should/shouldn't match
    def checkre(pat,ok,nok):
        for s in ok:
            assert re.fullmatch(pat,s), \
                f"pattern '{pat}'\n did not match string '{s}'"
        for s in nok:
            assert not re.fullmatch(pat,s), \
                f"pattern '{pat}'\n matched string '{s}'"  
    
    # list of n words with nl letters from chars without repeats
    def randwords(n,chars=string.ascii_lowercase,nl=(2,5)):
        l = []
        while len(l)<n:
            w = ''.join([chars[randint(0,len(chars)-1)] for i in range(randint(*nl))])
            if w not in l:
                l.append(w)
        return l
    
    # convert sets to dicts and dict keys to strings so they can be sorted
    def orderkeys(o):
        if isinstance(o,set):
            return {str(k):None for k in o}
        if isinstance(o,dict):
            return {str(k):orderkeys(v) for k,v in o.items()}
        return o
    

    def Q1():
        r = 10*random.random()
        ro = copy.deepcopy(r)
        a = area(r)
        return round(a,2),f"area({ro}) returns {a}"

    def Q2():
        l = randwords(randint(5,8),nl=(2,5))
        l = [s.upper() if randint(0,1) else s for s in l]
        ol = copy.deepcopy(l)
        noshout(l)
        return l,f"noshout({ol}) sets list to {l}"

    def Q3():
        k = randwords(10,nl=(3,7))
        v = randwords(10,nl=(5,10))
        f = [s for s in k if randint(0,1)]
        d = dict(zip(k,v))
        od, of = copy.deepcopy(d), copy.deepcopy(f)
        r = dfilt(d,f)
        return r,f"dfilt({od},{of}) returns {r}"
    
    def Q4():
        t=[randint(10,10000)/10 for i in range(randint(2,4))]
        ot=copy.deepcopy(t)
        r = [hms(x) for x in t]
        return r,f"hms() applied to value in {ot} returns {r}"

    def Q5():
        l=[(randint(1,100)/10,randint(1,100)/10) for i in range(randint(2,5))]
        ol=copy.deepcopy(l)
        r=areasum(l)
        return r,f"areasum({ol}) returns {r}"
   
    hashvalues = '''
OkJau47mBTO7u/g8acEtvVzzNpcIK8uOCwPQ6WWc
aEiekTPsWrzD4Bz1y4Bho8V53SQ6tFCgWbidNLUt
uc03EzamOycENPDx8skWvQCBnr6Vq7sB53ee/4x8
UsCp5keEsNSHgCSx6pLGnwSPTGMmCj5vndYZP/Oy
PznmH4BKBEpAUf1XHHp1w5xx8CVgf9+4v1kjJ3au
'''.split()

    newhash = ''
    dsize = 3 # HMAC base64 digest size (bytes, use 3 or 6 for 4 or 8 char digests)
    dlen = ((dsize*8+5)//6+3)//4*4
           
    for n,f in [(n,f) for n,f in locals().items() if callable(f) and re.search(r'^[Qq]\d+.*',n)]:
        random.seed(n)      
        hashes = '0'*dlen*ntest if testing else hashvalues.pop(0)
        err = ''
        while hashes and not err:
            h, hashes = hashes[:dlen], hashes[dlen:] 
            try:
                v,s = f()
                b = json.dumps(orderkeys(v),sort_keys=True).encode()
                c = base64.b64encode(hashlib.blake2b(b,digest_size=dsize).digest()).decode()
                if testing:
                    print(s)
                    newhash += c
                else:
                    if c != h:
                        err = f"Wrong result for test {n}: {s} (HMAC={c} instead of {h})"
            except Exception as e:
                err = f"Error during test {n}: {e}"               
        if testing:
            newhash += '\n'
        else:
            print(err or f"Passed test {n}.")
            
    if testing:
        print(newhash)

labcheck(0)